In [2]:
import json

In [3]:
path = "/home/sivakrishna/Documents/jupyter/finetuning-test/interviewer_tuning/data/interview-conv.txt"
file = open(path, 'r', encoding='utf-8')
content = file.read()
file.close()

In [4]:
# content = content[:9772]
# content += "\n]\n}"

In [5]:
def conv_to_dict(content):
    ret_conv = []
    for conv in content.split("["):
        qn_lst = []
        ans_lst = []
        for i in range(20, len(conv)):
            if conv[i-13: i] == '"question": "':
                segment_text = ""
                idx = i
                while True:
                    try:
                        if conv[idx] != '"':
                            segment_text += conv[idx]
                            idx += 1
                        else:
                            break
                    except:
                        break
                qn_lst.append(segment_text)
                i = idx
            elif conv[i-11: i] == '"answer": "':
                segment_text = ""
                idx = i
                while True:
                    try:
                        if conv[idx] != '"':
                            segment_text += conv[idx]
                            idx += 1
                        else:
                            break
                    except:
                        break
                ans_lst.append(segment_text)
                i = idx
    
        conv_lst = []
        for i in range(len(qn_lst)):
            try:
                conv_lst.append({"interviewer": qn_lst[i], "interviewee": ans_lst[i]})
            except Exception:
                continue
        ret_conv.append(conv_lst)
        
    return ret_conv

In [6]:
def filter_conv(conv_list):
    ret_list = [] 
    for i in conv_list:
        if len(i) != 0:
            ret_list.append(i)
        else:
            continue
    return ret_list

In [7]:
conv_lst = filter_conv(conv_to_dict(content))
conv_lst

[[{'interviewer': "Hi, I'm Lucy! I'll be interviewing you for the React.js job. Are you ready to get started, Modern Silpi?",
   'interviewee': 'hello Lucy yeah I am ready to take the to give my interview for react this job'},
  {'interviewer': "Great to hear, Modern Silpi! Let's start with the first question:",
   'interviewee': 'yeah sure please go ahead'},
  {'interviewer': 'Can you explain the concept of state in React?',
   'interviewee': 'yeah like the concept of estate is used to change something like for example we have given some initial default value so we can if some that point is clicked or done something some thing with that things then we can change its default value to our requirement you have to import the state on the top like import use State from react like that and then you can use it in our code to show the changes'},
  {'interviewer': "That's a good explanation, Modern Silpi! Here's the next question:",
   'interviewee': 'yeah please get me the next question'},
  

In [8]:
gen_conv_lst = []
for conv in conv_lst:
    for i in range(1, len(conv)):
        temp_conv = []
        for exchange in conv[:i]:
            temp_conv.append(exchange)
        gen_conv_lst.append(temp_conv)

In [9]:
gen_conv_lst

[[{'interviewer': "Hi, I'm Lucy! I'll be interviewing you for the React.js job. Are you ready to get started, Modern Silpi?",
   'interviewee': 'hello Lucy yeah I am ready to take the to give my interview for react this job'}],
 [{'interviewer': "Hi, I'm Lucy! I'll be interviewing you for the React.js job. Are you ready to get started, Modern Silpi?",
   'interviewee': 'hello Lucy yeah I am ready to take the to give my interview for react this job'},
  {'interviewer': "Great to hear, Modern Silpi! Let's start with the first question:",
   'interviewee': 'yeah sure please go ahead'}],
 [{'interviewer': "Hi, I'm Lucy! I'll be interviewing you for the React.js job. Are you ready to get started, Modern Silpi?",
   'interviewee': 'hello Lucy yeah I am ready to take the to give my interview for react this job'},
  {'interviewer': "Great to hear, Modern Silpi! Let's start with the first question:",
   'interviewee': 'yeah sure please go ahead'},
  {'interviewer': 'Can you explain the concept 

In [10]:
len(gen_conv_lst)

3900

In [11]:
def gen_prompt(conv_lst):
    INSTRUCTION = "### Instruction: You are an interviwer who intends to test the interviewee's technical capabilities by asking proper follow-up question based on your previous conversation with the interviewee.\n\n"
    CONTEXT = "### Conversation: \n"
    RESPONSE = "### Output: "

    prompt_lst = []
    
    for conv in conv_lst:
        conv_len = len(conv)
        temp_conv, idx = INSTRUCTION + CONTEXT, 0
        for exchange in conv:
            idx += 1
            if idx == conv_len:
                temp_conv += ("\n" + RESPONSE + exchange["interviewer"] + "\n")
            else:
                temp_conv += ("interviewer: " + exchange["interviewer"] + "\n" + "interviewee: " + exchange["interviewee"] + "\n")
        prompt_lst.append({"text": temp_conv})

    return prompt_lst

In [12]:
prompt_lst = gen_prompt(gen_conv_lst)

In [13]:
len(prompt_lst)

3900

In [14]:
for i in (prompt_lst[:250]):
    print(i, end="\n\n\n")

{'text': "### Instruction: You are an interviwer who intends to test the interviewee's technical capabilities by asking proper follow-up question based on your previous conversation with the interviewee.\n\n### Conversation: \n\n### Output: Hi, I'm Lucy! I'll be interviewing you for the React.js job. Are you ready to get started, Modern Silpi?\n"}


{'text': "### Instruction: You are an interviwer who intends to test the interviewee's technical capabilities by asking proper follow-up question based on your previous conversation with the interviewee.\n\n### Conversation: \ninterviewer: Hi, I'm Lucy! I'll be interviewing you for the React.js job. Are you ready to get started, Modern Silpi?\ninterviewee: hello Lucy yeah I am ready to take the to give my interview for react this job\n\n### Output: Great to hear, Modern Silpi! Let's start with the first question:\n"}


{'text': "### Instruction: You are an interviwer who intends to test the interviewee's technical capabilities by asking pro

In [15]:
conv_dict = {"data": prompt_lst}

In [16]:
with open("data/conv_data.json", "w") as file:
    json.dump(conv_dict, file, indent=4)